# Creating the NENA Speech Dataset

Download validated examples from Pocketbase

In [1]:
from pocketbase import PocketBase

pb = PocketBase('https://pocketbase.nenadb.dev/')

dialects = pb.collection("dialects").get_full_list(query_params={
    "sort": "name",
})

examples = pb.collection("examples").get_full_list(query_params={
    "expand": "dialect",
    "filter": "validated=true",
})

Create shards

In [ ]:
from pydub import AudioSegment
import requests
import tempfile

test_split = 0.10
dev_split = 0.10

for i, example in enumerate(examples):
    prog = i / len(examples)
    
    if prog < test_split:
        split = 'test'
    elif prog < dev_split + test_split:
        split = 'dev'
    else:
        split = 'train'

    audio_url = pb.get_file_url(example, example.speech, {})
    response = requests.get(audio_url)

    with tempfile.NamedTemporaryFile() as f:
        f.write(response.content)
        f.flush()
        audio = AudioSegment.from_file(f.name)

    audio = audio.set_frame_rate(48000)
    audio.export(f"nena_speech_{example.id}.mp3", format="mp3")

    break